## Search for Landsat-8 products using the "eop:track" as a queryable

In [1]:
import lxml.etree as etree
import requests
import cioppy
ciop = cioppy.Cioppy()

In [2]:
def get_params(osd):

    oss_ns = {'a':'http://www.w3.org/2001/XMLSchema', 
          'b':'http://www.w3.org/2001/XMLSchema-instance',
          'c':'http://a9.com/-/opensearch/extensions/time/1.0/',
          'd':'http://www.opengis.net/eop/2.0',
          'e':'http://purl.org/dc/terms/',
          'f':'http://a9.com/-/spec/opensearch/extensions/parameters/1.0/',
          'g':'http://purl.org/dc/elements/1.1/',
          'h':'http://www.terradue.com/opensearch',
          'i':'http://a9.com/-/opensearch/extensions/geo/1.0/',
          'j':'http://a9.com/-/spec/opensearch/1.1/'}
    
    oss_content = etree.fromstring(requests.get(osd).content)
    
    url_template_element = oss_content.xpath('/j:OpenSearchDescription/j:Url[@type="application/atom+xml"]',
                                                 namespaces=oss_ns)[0]
    
    parameters = dict()
    
    for index, parameter in enumerate(url_template_element.xpath('.//f:Parameter', namespaces=oss_ns)):
        
        parameters[parameter.attrib['name']] = {'title' : parameter.attrib['title'], 
                                                'value' : parameter.attrib['value']}
        
        options = []
        for option in parameter.xpath('.//f:Option', namespaces=oss_ns):
            
            options.append(option.attrib['value'])
    
        parameters[parameter.attrib['name']] = {'title' : parameter.attrib['title'], 
                                                'value' : parameter.attrib['value'],
                                                'options' : options}
    return parameters

In [3]:
def get_param_value(osd, os_parameter):

    params = get_params(osd)

    res = None
    
    for index, param in enumerate(params):
        
        if params[param]['value'] == os_parameter:
            
            res = params[param]
            res['name'] = param
     
    return res

Define the Landsat-8 endpoint

In [4]:
osd_url = 'https://catalog.terradue.com/landsat8/description'

Get the Landsat-8 search parameters

In [5]:
ls8_parameters = get_params(osd_url)

Print all the OpenSearch parameters

In [6]:
for key, value in ls8_parameters.iteritems():

    print '%24s' % ls8_parameters[key]['value'],  ls8_parameters[key]['title'] 

              {geo:uid?} The identifier of the resource within the search engine context (local reference)
    {t2:downloadOrigin?} a string that identifies the download origin (keyword, hostname...) to adapt the enclosure. If the parameter is enclosed between [] (e.g. [terradue]), enclosure will be returned only if there is a enclosure found for this source.
       {eop:cloudCover?} A number, set or interval requesting the cloud coverage
            {eop:frame?} A number, set or interval requesting the range of orbit frames
            {startIndex} index of the first search result desired
   {t2:vendorSpecifics?} A number, set or interval filtering vendor specific name:value
             {startPage} page number of the set of search results desired
       {eop:sensorType?} A string identifying the sensor type
     {eop:accessedFrom?} A string identifying the location from which the resource will be accessed. The catalogue shall return the download location in the enclosure atom link ac

Find the parameter associated to **'{eop:wrsLongitudeGrid?}'** and its options

In [7]:
product_type_parameter = get_param_value(osd_url, '{eop:track?}')
download_origin_parameter = get_param_value(osd_url, '{t2:downloadOrigin?}')

In [8]:
product_type_parameter['name']

'track'

Now search for Landsat-8 products creating a dictionary with the search parameters

In [9]:
search_params = dict([(product_type_parameter['name'], 
                       '160'), (download_origin_parameter['name'], 'terradue')])

In [10]:
search_params

{'do': 'terradue', 'track': '160'}

In [11]:
search = ciop.search(end_point=osd_url,
                     params=search_params,
                     output_fields='self,productType,track,enclosure,identifier,wkt,startdate', 
                     model='EOP')

Show the first result returned

In [12]:
search[0]

{'enclosure': 'https://store.terradue.com/download/landsat8/files/v1/LC08_L1TP_160248_20190430_20190430_01_RT',
 'identifier': 'LC08_L1TP_160248_20190430_20190430_01_RT',
 'productType': 'L1TP',
 'self': 'https://catalog.terradue.com/landsat8/search?format=atom&uid=LC08_L1TP_160248_20190430_20190430_01_RT',
 'startdate': '2019-04-30T08:07:29.6130000Z',
 'track': '160',
 'wkt': 'POLYGON((93.72898 81.78061,98.27937 80.20367,108.4065 80.72712,105.58942 82.40608,93.72898 81.78061))'}

You can of course write the search parameters directly with:


In [13]:
search = ciop.search(end_point=osd_url,
                     params={'track': '160'},
                     output_fields='self,productType,track,enclosure,identifier,wkt,startdate', 
                     model='EOP')

In [14]:
search[0]

{'enclosure': 'https://earthexplorer.usgs.gov/download/external/options/LANDSAT_8_C1/LC81602482019120LGN00/INVSVC/',
 'identifier': 'LC08_L1TP_160248_20190430_20190430_01_RT',
 'productType': 'L1TP',
 'self': 'https://catalog.terradue.com/landsat8/search?format=atom&uid=LC08_L1TP_160248_20190430_20190430_01_RT',
 'startdate': '2019-04-30T08:07:29.6130000Z',
 'track': '160',
 'wkt': 'POLYGON((93.72898 81.78061,98.27937 80.20367,108.4065 80.72712,105.58942 82.40608,93.72898 81.78061))'}